## Import Libraries - Data

In [7]:
import pandas as pd
import numpy as np
from gensim.models import Word2Vec
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA

#set the max columns to none
pd.set_option('display.max_columns', None)

In [110]:
# Raw data
size = 'small'
#articles_path = f'./files/parquet/ebnerd_{size}/articles.parquet'
#df_articles = pd.read_parquet(articles_path)

#Import train Data
behaviors_train_path = f'./files/parquet/ebnerd_{size}/train/behaviors.parquet'
history_train_path = f'./files/parquet/ebnerd_{size}/train/history.parquet'

behaviors_train_df = pd.read_parquet(behaviors_train_path)
history_train_df = pd.read_parquet(history_train_path)

#Import validation data
behaviors_val_path = f'./files/parquet/ebnerd_{size}/validation/behaviors.parquet'
history_val_path = f'./files/parquet/ebnerd_{size}/validation/history.parquet'

behaviors_val_df = pd.read_parquet(behaviors_val_path)
history_val_df = pd.read_parquet(history_val_path)

# Ready embeddings
#embeddings_path = f'./files/parquet/FacebookAI_xlm_roberta_base/xlm_roberta_base.parquet'
embeddings_path = f'./files/parquet/Ekstra_Bladet_word2vec/document_vector.parquet'
df_embeddings = pd.read_parquet(embeddings_path)

In [50]:
# print(df_articles.columns)
# print(df_articles.shape)
# df_articles.head(5)

In [118]:
# Columns of dataframes

print("Columns of behaviors_train_df:")
print(list(behaviors_train_df.columns))

print("\nColumns of history_train_df:")
print(list(history_train_df.columns))


Columns of behaviors_train_df:
['impression_id', 'article_id', 'impression_time', 'read_time', 'scroll_percentage', 'device_type', 'article_ids_inview', 'article_ids_clicked', 'user_id', 'is_sso_user', 'gender', 'postcode', 'age', 'is_subscriber', 'session_id', 'next_read_time', 'next_scroll_percentage']

Columns of history_train_df:
['user_id', 'impression_time_fixed', 'scroll_percentage_fixed', 'article_id_fixed', 'read_time_fixed']


In [120]:
# Shapes of dataframes

print("Shape of behaviors_train_df:         ", behaviors_train_df.shape)
print("Shape of behaviors_val_df:           ", behaviors_val_df.shape)
print("Shape of history_train_df:           ", behaviors_train_df.shape)
print("Shape of history_val_df:             ", behaviors_val_df.shape)


Shape of behaviors_train_df:          (232887, 17)
Shape of behaviors_val_df:            (244647, 17)
Shape of history_train_df:            (232887, 17)
Shape of history_val_df:              (244647, 17)


#### Use a specific user to check behaviors and history dataframes regarding the articles they contain

In [129]:
print(behaviors_train_df['impression_time'].min())
print(behaviors_train_df['impression_time'].max())
behaviors_train_df[behaviors_train_df['user_id']==139836]

2023-05-18 07:00:01
2023-05-25 06:59:58


impression_id  article_id     impression_time  read_time  \
0              149474         NaN 2023-05-24 07:47:53       13.0   
114236      285235071         NaN 2023-05-18 09:56:55       34.0   
114237      285235073         NaN 2023-05-18 09:56:35       16.0   
114238      285235075         NaN 2023-05-18 09:57:35        4.0   
114239      285235077         NaN 2023-05-18 09:59:12       35.0   
138189      344665040         NaN 2023-05-20 15:22:31        7.0   
138190      344665041         NaN 2023-05-20 15:21:59       29.0   
138191      344665043         NaN 2023-05-20 15:21:04       14.0   

        scroll_percentage  device_type  \
0                     NaN            2   
114236                NaN            2   
114237                NaN            2   
114238                NaN            2   
114239                NaN            2   
138189                NaN            2   
138190                NaN            2   
138191                NaN            2   

                                       article_ids_inview article_ids_clicked  \
0       [9778623, 9778682, 9778669, 9778657, 9778736, ...           [9778657]   
114236  [9770997, 9769306, 9767697, 9771128, 9771166, ...           [9770997]   
114237      [9771065, 9771166, 9771253, 9771126, 9771242]           [9771065]   
114238      [9695098, 9769306, 9770997, 9746360, 9771042]           [9769306]   
114239  [9769762, 9233208, 9771126, 9770997, 9771166, ...           [9771042]   
138189  [9531745, 9773493, 9773434, 9773488, 9771113, ...           [9771113]   
138190  [9773638, 9769624, 9773275, 9773364, 9773539, ...           [9773364]   
138191  [9773700, 9773644, 9773744, 9746810, 9755800, ...           [9746810]   

        user_id  is_sso_user  gender  postcode  age  is_subscriber  \
0        139836        False     NaN       NaN  NaN          False   
114236   139836        False     NaN       NaN  NaN          False   
114237   139836        False     NaN       NaN  NaN          False   
114238   139836        False     NaN       NaN  NaN          False   
114239   139836        False     NaN       NaN  NaN          False   
138189   139836        False     NaN       NaN  NaN          False   
138190   139836        False     NaN       NaN  NaN          False   
138191   139836        False     NaN       NaN  NaN          False   

        session_id  next_read_time  next_scroll_percentage  
0              759             7.0                    22.0  
114236         755             4.0                    39.0  
114237         755             3.0                    18.0  
114238         755            56.0                    75.0  
114239         755             4.0                    42.0  
138189         757            16.0                   100.0  
138190         757             2.0                    22.0  
138191         757            14.0                    52.0

In [130]:
print(behaviors_val_df['impression_time'].min())
print(behaviors_val_df['impression_time'].max())
behaviors_val_df[behaviors_val_df['user_id']==139836]

2023-05-25 07:00:02
2023-06-01 06:59:59


Empty DataFrame
Columns: [impression_id, article_id, impression_time, read_time, scroll_percentage, device_type, article_ids_inview, article_ids_clicked, user_id, is_sso_user, gender, postcode, age, is_subscriber, session_id, next_read_time, next_scroll_percentage]
Index: []

In [133]:
print(history_train_df['impression_time_fixed'][1])

history_train_df[history_train_df['user_id'] == 139836]

['2023-04-27T09:40:18.000000' '2023-04-27T09:40:33.000000'
 '2023-04-27T13:06:33.000000' '2023-04-27T13:07:07.000000'
 '2023-04-27T16:01:45.000000' '2023-04-27T16:03:16.000000'
 '2023-04-27T16:03:38.000000' '2023-04-27T16:03:53.000000'
 '2023-04-27T18:24:25.000000' '2023-04-27T23:00:36.000000'
 '2023-04-27T23:02:05.000000' '2023-04-27T23:02:08.000000'
 '2023-04-28T06:09:04.000000' '2023-04-28T08:11:09.000000'
 '2023-04-28T08:11:33.000000' '2023-04-28T09:38:08.000000'
 '2023-04-28T09:38:55.000000' '2023-04-28T09:41:08.000000'
 '2023-04-28T09:41:31.000000' '2023-04-28T11:42:01.000000'
 '2023-04-28T11:42:59.000000' '2023-04-28T11:43:22.000000'
 '2023-04-28T11:43:55.000000' '2023-04-30T16:06:44.000000'
 '2023-04-30T16:07:20.000000' '2023-05-01T07:11:39.000000'
 '2023-05-01T07:12:04.000000' '2023-05-01T07:12:19.000000'
 '2023-05-01T07:12:22.000000' '2023-05-01T11:25:06.000000'
 '2023-05-01T11:25:35.000000' '2023-05-01T11:55:24.000000'
 '2023-05-01T11:55:52.000000' '2023-05-01T12:32:28.00000

user_id                              impression_time_fixed  \
11894   139836  [2023-05-03T19:04:15.000000, 2023-05-03T19:05:...   

                                 scroll_percentage_fixed  \
11894  [100.0, 89.0, 27.0, 33.0, 100.0, 75.0, 39.0, 2...   

                                        article_id_fixed  \
11894  [9745590, 9748574, 9748432, 9748080, 9750687, ...   

                                         read_time_fixed  
11894  [60.0, 11.0, 1.0, 15.0, 37.0, 15.0, 4.0, 8.0, ...

In [135]:
print(history_val_df['impression_time_fixed'][0])
history_val_df[history_val_df['user_id'] == 139836]

['2023-05-04T12:42:38.000000' '2023-05-04T12:43:04.000000'
 '2023-05-04T17:04:39.000000' '2023-05-04T17:05:35.000000'
 '2023-05-04T17:06:22.000000' '2023-05-04T17:06:37.000000'
 '2023-05-04T18:26:26.000000' '2023-05-04T21:07:39.000000'
 '2023-05-04T21:08:02.000000' '2023-05-04T21:08:19.000000'
 '2023-05-04T21:08:32.000000' '2023-05-04T21:08:52.000000'
 '2023-05-05T07:22:47.000000' '2023-05-05T07:35:48.000000'
 '2023-05-05T07:36:15.000000' '2023-05-05T11:56:56.000000'
 '2023-05-05T11:57:58.000000' '2023-05-05T11:59:24.000000'
 '2023-05-05T17:37:35.000000' '2023-05-05T18:58:47.000000'
 '2023-05-05T18:59:22.000000' '2023-05-05T20:12:22.000000'
 '2023-05-05T20:12:53.000000' '2023-05-06T07:03:12.000000'
 '2023-05-06T07:03:55.000000' '2023-05-06T11:32:26.000000'
 '2023-05-06T11:32:47.000000' '2023-05-06T12:31:18.000000'
 '2023-05-06T12:31:53.000000' '2023-05-06T12:32:52.000000'
 '2023-05-06T12:59:13.000000' '2023-05-06T20:19:44.000000'
 '2023-05-07T07:41:32.000000' '2023-05-07T14:39:08.00000

Empty DataFrame
Columns: [user_id, impression_time_fixed, scroll_percentage_fixed, article_id_fixed, read_time_fixed]
Index: []

In [108]:
print("df_history Column names:                                  ", list(df_history.columns))
print("Shape of df_history dataframe:                            ", df_history.shape)

lst =  [9778657, 9770997, 9771065, 9769306, 9771042, 9771113, 9773364, 9746810] 
results = []
for elem in lst:
    results.append(elem in list(df_history[df_history['user_id'] == 139836]['article_id_fixed'].values[0]))

print("List of articles in df_behaviors for user 139836:         ", lst)
print("Check if the articles in df_history:                      ",results)
print("\nThe actual article ids in df_history:")
print(list(df_history[df_history['user_id'] == 139836]['article_id_fixed'].values[0]))


print("\n\n\nThe row of the df_history dataframe:")
df_history[df_history['user_id'] == 139836]

df_history Column names:                                   ['user_id', 'impression_time_fixed', 'scroll_percentage_fixed', 'article_id_fixed', 'read_time_fixed']
Shape of df_history dataframe:                             (15143, 5)
List of articles in df_behaviors for user 139836:          [9778657, 9770997, 9771065, 9769306, 9771042, 9771113, 9773364, 9746810]
Check if the articles in df_history:                       [False, False, False, False, False, False, False, False]

The actual article ids in df_history:
[9745590, 9748574, 9748432, 9748080, 9750687, 9750802, 9750829, 9750793, 9750726, 9748041, 4800276, 9757533, 9760252, 9760528, 9760272, 9760067, 9765336, 9765185, 9765156]



The row of the df_history dataframe:


user_id                              impression_time_fixed  \
11894   139836  [2023-05-03T19:04:15.000000, 2023-05-03T19:05:...   

                                 scroll_percentage_fixed  \
11894  [100.0, 89.0, 27.0, 33.0, 100.0, 75.0, 39.0, 2...   

                                        article_id_fixed  \
11894  [9745590, 9748574, 9748432, 9748080, 9750687, ...   

                                         read_time_fixed  
11894  [60.0, 11.0, 1.0, 15.0, 37.0, 15.0, 4.0, 8.0, ...

### I am checking my data and i can see that in df_history for an example user 139836 i have some articles that he clicked (I GUESS) and for the same user in df_behaviors the same user for columns article_ids_clicked non of the ids is in the data of df_history

In [67]:
## Specify the path to your text file
file_path = './files/parquet/predictions.txt'

# Initialize lists to store parsed data
keys = []
values = []

# Open the file in read mode
with open(file_path, 'r') as file:
    # Read each line in the file
    for line in file:
        # Strip any leading/trailing whitespace characters
        line = line.strip()
        
        # Extract the key (number before the '[' character)
        key_start = line.find(' ')
        key = int(line[:key_start])
        
        # Extract the value (list of integers inside the brackets)
        value_str = line[key_start:]
        value = [int(num) for num in value_str.strip()[1:-1].split(',')]  # Extract and convert to list of integers
        
        # Append key and value to lists
        keys.append(key)
        values.append(value)

# Create a DataFrame from the lists of keys and values
df = pd.DataFrame({'Key': keys, 'Value': values})



NameError: name 'article_id_fixed' is not defined

In [13]:
df

Key                                              Value
0         6451339                        [8, 1, 6, 7, 4, 2, 9, 5, 3]
1         6451363                           [5, 4, 3, 7, 6, 8, 1, 2]
2         6451382                                    [1, 5, 3, 4, 2]
3         6451383                [7, 6, 8, 9, 3, 4, 2, 11, 10, 1, 5]
4         6451385                              [5, 3, 2, 4, 7, 6, 1]
...           ...                                                ...
13536705        0  [120, 49, 179, 32, 30, 42, 155, 50, 45, 234, 9...
13536706        0  [248, 62, 36, 2, 152, 199, 241, 235, 155, 160,...
13536707        0  [163, 77, 143, 232, 69, 16, 27, 119, 186, 166,...
13536708        0  [113, 233, 67, 105, 130, 8, 100, 173, 158, 28,...
13536709        0  [142, 17, 248, 67, 201, 159, 163, 219, 22, 40,...

[13536710 rows x 2 columns]

## I will create two tables with embeddings, one will come from df_articles and the other from the other two dfs joined. I will try firstly the embeddings that are provided and more specificaly the word2vec embeddings, in order to create a proof of concept. After that if it is needed i will begin from the raw data to build the embeddings from scratch.

## Pre process df_articles

In [14]:
df_embeddings

article_id                                    document_vector
0          3000022  [0.06542388, -0.047424573, 0.06384871, -0.0014...
1          3000063  [0.028815078, -0.00016637295, 0.055056807, 0.0...
2          3000613  [0.037971217, 0.03392251, 0.027297212, 0.01708...
3          3000700  [0.04652399, 0.0029133065, 0.06280604, -0.0051...
4          3000840  [0.014736942, 0.024067875, 0.0051865038, 0.041...
...            ...                                                ...
125536     9803505  [0.029624538, -0.039833125, -0.03009815, 0.005...
125537     9803510  [-0.0284717, -0.035652492, 0.027552828, -0.018...
125538     9803525  [0.039465133, 0.00079695834, 0.062067263, 0.08...
125539     9803560  [0.0049191406, 0.01373551, 0.020911952, 0.0108...
125540     9803607  [0.0005135782, -0.046943206, 0.054680478, 0.02...

[125541 rows x 2 columns]

In [15]:
df_articles.head()

article_id                                       title  \
0     3037230  Ishockey-spiller: Jeg troede jeg skulle dø   
1     3044020            Prins Harry tvunget til dna-test   
2     3057622                 Rådden kørsel på blå plader   
3     3073151                   Mærsk-arvinger i livsfare   
4     3193383              Skød svigersøn gennem babydyne   

                                            subtitle  last_modified_time  \
0  ISHOCKEY: Ishockey-spilleren Sebastian Harts h... 2023-06-29 06:20:57   
1  Hoffet tvang Prins Harry til at tage dna-test ... 2023-06-29 06:21:16   
2  Kan ikke straffes: Udenlandske diplomater i Da... 2023-06-29 06:21:24   
3  FANGET I FLODBØLGEN: Skibsrederens oldebørn må... 2023-06-29 06:21:38   
4  44-årig kvinde tiltalt for drab på ekssvigersø... 2023-06-29 06:22:57   

   premium                                               body  \
0    False  Ambitionerne om at komme til USA og spille ish...   
1    False  Den britiske tabloidavis The Sun fortsætter me...   
2    False  Slingrende spritkørsel. Grove overtrædelser af...   
3    False  To oldebørn af skibsreder Mærsk McKinney Mølle...   
4    False  En 44-årig mormor blev i dag fremstillet i et ...   

       published_time                    image_ids     article_type  \
0 2003-08-28 08:55:00                         None  article_default   
1 2005-06-29 08:47:00  [3097307, 3097197, 3104927]  article_default   
2 2005-10-10 07:20:00                    [3047102]  article_default   
3 2005-01-04 06:59:00  [3067474, 3067478, 3153705]  article_default   
4 2003-09-15 15:30:00                         None  article_default   

                                                 url           ner_clusters  \
0  https://ekstrabladet.dk/sport/anden_sport/isho...                     []   
1  https://ekstrabladet.dk/underholdning/udlandke...  [Harry, James Hewitt]   
2  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
3  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
4   https://ekstrabladet.dk/krimi/article3193383.ece                     []   

  entity_groups                                             topics  category  \
0            []  [Kriminalitet, Kendt, Sport, Katastrofe, Mindr...       142   
1    [PER, PER]  [Kriminalitet, Kendt, Underholdning, Personfar...       414   
2            []               [Kriminalitet, Transportmiddel, Bil]       118   
3            []  [Erhverv, Privat virksomhed, Livsstil, Familie...       118   
4            []          [Kriminalitet, Personfarlig kriminalitet]       140   

  subcategory   category_str  total_inviews  total_pageviews  total_read_time  \
0  [327, 334]          sport            NaN              NaN              NaN   
1       [432]  underholdning            NaN              NaN              NaN   
2       [133]        nyheder            NaN              NaN              NaN   
3       [133]        nyheder            NaN              NaN              NaN   
4          []          krimi            NaN              NaN              NaN   

   sentiment_score sentiment_label  
0           0.9752        Negative  
1           0.7084        Negative  
2           0.9236        Negative  
3           0.9945        Negative  
4           0.9966        Negative

In [16]:
df_articles.isnull().sum()

article_id               0
title                    0
subtitle                 0
last_modified_time       0
premium                  0
body                     0
published_time           0
image_ids              937
article_type             0
url                      0
ner_clusters             0
entity_groups            0
topics                   0
category                 0
subcategory              0
category_str             0
total_inviews         4271
total_pageviews       4271
total_read_time       4271
sentiment_score          0
sentiment_label          0
dtype: int64

In [17]:
#df_articles = df_articles.drop(["image_ids", "total_inviews", "total_pageviews", "total_read_time", "last_modified_time", "published_time", "url"], axis= 1)

df_articles = df_articles[["article_id"]]

In [18]:
df_articles.head()

article_id
0     3037230
1     3044020
2     3057622
3     3073151
4     3193383

In [19]:
df_articles_embeddings = pd.merge(df_articles, df_embeddings, on="article_id") 

In [20]:
df_articles_embeddings.head()

article_id                                    document_vector
0     3037230  [0.017898837, -0.012223162, 0.0117029, 0.03572...
1     3044020  [0.041870505, 0.002982251, 0.07588886, -0.0031...
2     3057622  [0.03602814, -0.004919843, -0.005812604, 0.015...
3     3073151  [0.039754465, -0.014155321, 0.044064052, 0.040...
4     3193383  [0.014357477, -0.07686433, 0.07009871, 0.02835...

In [21]:
df_articles_embeddings = df_articles_embeddings.set_index('article_id')

In [22]:
df_articles_embeddings.head()

document_vector
article_id                                                   
3037230     [0.017898837, -0.012223162, 0.0117029, 0.03572...
3044020     [0.041870505, 0.002982251, 0.07588886, -0.0031...
3057622     [0.03602814, -0.004919843, -0.005812604, 0.015...
3073151     [0.039754465, -0.014155321, 0.044064052, 0.040...
3193383     [0.014357477, -0.07686433, 0.07009871, 0.02835...

In [23]:
def unpack_lists(df, column_name):
    # Create new columns by unpacking lists in the specified column
    unpacked_cols = pd.DataFrame(df[column_name].tolist(), index=df.index)
    # Rename the columns with a prefix based on the original column name
    unpacked_cols = unpacked_cols.add_prefix(column_name + '_')
    # Concatenate the unpacked columns back to the original DataFrame
    df = pd.concat([df, unpacked_cols], axis=1)
    return df

# Specify which columns to process
columns_to_process = ['document_vector']

# Unpack lists in each specified column
for col in columns_to_process:
    df_articles_embeddings = unpack_lists(df_articles_embeddings, col)

In [24]:
df_articles_embeddings.drop('document_vector', axis=1, inplace=True)

In [25]:
df_articles_embeddings.shape

(11777, 300)

## Pre process df_behaviors and df_history

In [26]:
# df_behaviors.isnull().sum()
# df_behaviors = df_behaviors.drop(["impression_id","impression_time", "scroll_percentage", "gender", "postcode","age","article_id", "next_read_time", "next_scroll_percentage"], axis=1)
# df_behaviors.isnull().sum()
# df_users = pd.merge(df_behaviors, df_history, on="user_id") 

In [27]:
df_users = df_history.copy()

In [28]:
df_users =df_users.drop(["impression_time_fixed"], axis=1)

In [29]:
df_users.head()

user_id                            scroll_percentage_fixed  \
0    13538  [100.0, 35.0, 100.0, 24.0, 100.0, 23.0, 100.0,...   
1    58608  [37.0, 61.0, 100.0, 100.0, 55.0, 100.0, 100.0,...   
2    95507  [60.0, 100.0, 100.0, 21.0, 29.0, 67.0, 49.0, 5...   
3   106588  [24.0, 57.0, 100.0, nan, nan, 100.0, 100.0, 73...   
4   617963  [100.0, 100.0, nan, 46.0, 23.0, 19.0, 61.0, 70...   

                                    article_id_fixed  \
0  [9738663, 9738569, 9738663, 9738490, 9738663, ...   
1  [9739362, 9739179, 9738567, 9739344, 9739202, ...   
2  [9739035, 9738646, 9634967, 9738902, 9735495, ...   
3  [9738292, 9738216, 9737266, 9737556, 9737657, ...   
4  [9739035, 9739088, 9738902, 9738968, 9738760, ...   

                                     read_time_fixed  
0  [17.0, 12.0, 4.0, 5.0, 4.0, 9.0, 5.0, 46.0, 11...  
1  [2.0, 24.0, 72.0, 65.0, 11.0, 4.0, 101.0, 0.0,...  
2  [18.0, 29.0, 51.0, 12.0, 10.0, 10.0, 13.0, 24....  
3  [9.0, 15.0, 42.0, 9.0, 3.0, 58.0, 26.0, 214.0,...  
4  [45.0, 29.0, 116.0, 26.0, 34.0, 42.0, 58.0, 59...

In [30]:
# for col in ["is_sso_user", "is_subscriber"]:
#     df_users[col] = df_users[col].replace({False: 0, True: 1})

In [31]:
# def has_na(x):
#     if np.nan in x:
#         return True
#     else:
#         return False

In [32]:
# for col in ["article_ids_inview", "scroll_percentage_fixed", "read_time_fixed","article_id_fixed", "article_ids_clicked"]:
#     df_users[col+"_nans"] = df_users[col].map(has_na)
#     print(df_users[col+"_nans"].unique())

## Nans do not exist inside the lists

In [33]:
# df_users = df_users.drop(["article_ids_inview_nans", "read_time_fixed_nans", "scroll_percentage_fixed_nans", "article_id_fixed_nans", "article_ids_clicked_nans"], axis=1)

In [34]:
df_users.head()

user_id                            scroll_percentage_fixed  \
0    13538  [100.0, 35.0, 100.0, 24.0, 100.0, 23.0, 100.0,...   
1    58608  [37.0, 61.0, 100.0, 100.0, 55.0, 100.0, 100.0,...   
2    95507  [60.0, 100.0, 100.0, 21.0, 29.0, 67.0, 49.0, 5...   
3   106588  [24.0, 57.0, 100.0, nan, nan, 100.0, 100.0, 73...   
4   617963  [100.0, 100.0, nan, 46.0, 23.0, 19.0, 61.0, 70...   

                                    article_id_fixed  \
0  [9738663, 9738569, 9738663, 9738490, 9738663, ...   
1  [9739362, 9739179, 9738567, 9739344, 9739202, ...   
2  [9739035, 9738646, 9634967, 9738902, 9735495, ...   
3  [9738292, 9738216, 9737266, 9737556, 9737657, ...   
4  [9739035, 9739088, 9738902, 9738968, 9738760, ...   

                                     read_time_fixed  
0  [17.0, 12.0, 4.0, 5.0, 4.0, 9.0, 5.0, 46.0, 11...  
1  [2.0, 24.0, 72.0, 65.0, 11.0, 4.0, 101.0, 0.0,...  
2  [18.0, 29.0, 51.0, 12.0, 10.0, 10.0, 13.0, 24....  
3  [9.0, 15.0, 42.0, 9.0, 3.0, 58.0, 26.0, 214.0,...  
4  [45.0, 29.0, 116.0, 26.0, 34.0, 42.0, 58.0, 59...

## Unpack list in columns

In [35]:
def unpack_lists(df, column_name):
    # Create new columns by unpacking lists in the specified column
    unpacked_cols = pd.DataFrame(df[column_name].tolist(), index=df.index)
    # Rename the columns with a prefix based on the original column name
    unpacked_cols = unpacked_cols.add_prefix(column_name + '_')
    # Concatenate the unpacked columns back to the original DataFrame
    df = pd.concat([df, unpacked_cols], axis=1)
    return df

# Specify which columns to process
# columns_to_process = ['article_ids_inview', 'article_ids_clicked', 'scroll_percentage_fixed', 'article_id_fixed', 'read_time_fixed']
columns_to_process = ['scroll_percentage_fixed', 'article_id_fixed', 'read_time_fixed']

# Unpack lists in each specified column
for col in columns_to_process:
    df_users = unpack_lists(df_users, col)


In [36]:
df_users = df_users.drop(columns_to_process, axis=1)

In [37]:
df_users = df_users.set_index('user_id')

In [38]:
df_users

scroll_percentage_fixed_0  scroll_percentage_fixed_1  \
user_id                                                         
13538                        100.0                       35.0   
58608                         37.0                       61.0   
95507                         60.0                      100.0   
106588                        24.0                       57.0   
617963                       100.0                      100.0   
...                            ...                        ...   
1122370                      100.0                      100.0   
1718049                       53.0                      100.0   
1178033                        NaN                       98.0   
395912                       100.0                      100.0   
2539047                       46.0                      100.0   

         scroll_percentage_fixed_2  scroll_percentage_fixed_3  \
user_id                                                         
13538                        100.0                       24.0   
58608                        100.0                      100.0   
95507                        100.0                       21.0   
106588                       100.0                        NaN   
617963                         NaN                       46.0   
...                            ...                        ...   
1122370                      100.0                      100.0   
1718049                       24.0                      100.0   
1178033                       92.0                       30.0   
395912                       100.0                       33.0   
2539047                       40.0                      100.0   

         scroll_percentage_fixed_4  scroll_percentage_fixed_5  \
user_id                                                         
13538                        100.0                       23.0   
58608                         55.0                      100.0   
95507                         29.0                       67.0   
106588                         NaN                      100.0   
617963                        23.0                       19.0   
...                            ...                        ...   
1122370                        NaN                        NaN   
1718049                       83.0                       28.0   
1178033                       35.0                        9.0   
395912                         NaN                        NaN   
2539047                      100.0                      100.0   

         scroll_percentage_fixed_6  scroll_percentage_fixed_7  \
user_id                                                         
13538                        100.0                      100.0   
58608                        100.0                        NaN   
95507                         49.0                       54.0   
106588                       100.0                       73.0   
617963                        61.0                       70.0   
...                            ...                        ...   
1122370                        NaN                        NaN   
1718049                       37.0                       40.0   
1178033                       34.0                       58.0   
395912                         NaN                        NaN   
2539047                       28.0                      100.0   

         scroll_percentage_fixed_8  scroll_percentage_fixed_9  \
user_id                                                         
13538                        100.0                       26.0   
58608                         61.0                      100.0   
95507                         25.0                       19.0   
106588                        26.0                       30.0   
617963                        64.0                       72.0   
...                            ...                        ...   
1122370                        NaN                        NaN   
1718049                       22.0      

In [39]:
def create_pca_embeddings(df, columns, n_components):
    # Fill NaN values with a default value (-999)
    df_filled = df[columns].fillna(-999)
    
    # Initialize PCA model
    pca = PCA(n_components=n_components)
    
    # Fit PCA on the numerical data
    embeddings = pca.fit_transform(df_filled.values)
    
    # Create a new DataFrame to store PCA embeddings with the same index as the original DataFrame
    embeddings_df = pd.DataFrame(embeddings, index=df.index)
    
    # Rename columns of the embeddings DataFrame
    embeddings_df.columns = [f'pca_embedding_{i}' for i in range(n_components)]
    
    return embeddings_df

In [40]:
# Specify columns to apply embeddings
columns_for_embeddings = list(df_users.columns)

# Apply PCA embeddings to ID columns
df_users_embeddings = create_pca_embeddings(df_users, columns_for_embeddings, n_components=300)

In [41]:
df_users_embeddings

pca_embedding_0  pca_embedding_1  pca_embedding_2  pca_embedding_3  \
user_id                                                                       
13538       1.524437e+08     7.024936e+07     2.424417e+07    -4.800035e+06   
58608       6.188810e+05    -4.392026e+07     2.797433e+07     5.439820e+06   
95507       1.054429e+08    -8.282102e+06    -4.236038e+07    -2.434165e+07   
106588     -6.160550e+05    -4.314132e+07     2.848665e+07     4.230237e+06   
617963      6.778455e+07    -4.299940e+07    -3.036714e+07     1.598942e+07   
...                  ...              ...              ...              ...   
1122370    -6.293004e+07     3.137580e+07    -2.105634e+07     1.663342e+07   
1718049    -6.276366e+07     3.107744e+07    -2.061967e+07     1.602400e+07   
1178033    -6.276408e+07     3.107821e+07    -2.062078e+07     1.602556e+07   
395912     -6.293004e+07     3.137579e+07    -2.105636e+07     1.663344e+07   
2539047    -6.215212e+07     2.997349e+07    -1.903626e+07     1.384987e+07   

         pca_embedding_4  pca_embedding_5  pca_embedding_6  pca_embedding_7  \
user_id                                                                       
13538      -1.913102e+07    -2.804426e+07    -2.275579e+07    -1.847000e+07   
58608      -2.084014e+07     9.453188e+06     7.442964e+06    -1.142627e+07   
95507       3.451099e+06     2.239256e+07     1.253899e+07    -3.892277e+06   
106588     -2.045310e+07     1.024573e+07     6.415888e+06    -1.154919e+07   
617963      2.340479e+07    -3.429266e+06    -1.649835e+07    -3.407469e+06   
...                  ...              ...              ...              ...   
1122370    -1.279853e+07     9.319078e+06    -9.918904e+06     7.158301e+06   
1718049    -1.208053e+07     8.556942e+06    -8.838233e+06     6.158039e+06   
1178033    -1.208237e+07     8.558904e+06    -8.841042e+06     6.160611e+06   
395912     -1.279856e+07     9.319102e+06    -9.918917e+06     7.158339e+06   
2539047    -9.565259e+06     5.940312e+06    -5.186841e+06     2.899692e+06   

         pca_embedding_8  pca_embedding_9  pca_embedding_10  pca_embedding_11  \
user_id                                                                         
13538      -4.554227e+06     7.486377e+06      1.202081e+07      1.674945e+07   
58608       4.813609e+06     5.422490e+06     -8.498500e+06     -1.245145e+05   
95507      -1.419121e+07    -4.671329e+06      5.457152e+06      9.468693e+06   
106588      5.830200e+06     4.527233e+06     -8.758907e+06      1.076175e+06   
617963      1.400487e+07     2.413570e+06     -1.005895e+07     -6.375482e+06   
...                  ...              ...               ...               ...   
1122370    -6.213981e+06     6.707649e+06     -7.065240e+06      5.260484e+06   
1718049    -5.123833e+06     5.279987e+06     -5.314119e+06      3.703353e+06   
1178033    -5.126716e+06     5.283721e+06     -5.318610e+06      3.707328e+06   
395912     -6.213941e+06     6.707699e+06     -7.065286e+06      5.260517e+06   
2539047    -1.672613e+06     8.593113e+05     -3.942732e+04     -8.176298e+05   

         pca_embedding_12  pca_embedding_13  pca_embedding_14  \
user_id                                                         
13538        1.107631e+07     -2.135642e+05     -8.219258e+06   
58608        4.404852e+06     -6.931038e+06     -8.720222e+05   
95507       -2.400122e+04     -8.869927e+06     -1.162876e+07   
106588       3.500167e+06     -7.580919e+06      2.939209e+05   
617963       8.710007e+06      6.359307e+06     -3.412634e+06   
...                   ...               ...               ...   
1122370     -4.766219e+06      5.708506e+06     -3.550131e+06   
1718049     -3.215844e+06      3.466178e+06     -1.939324e+06   
1178033     -3.219813e+06      3.471947e+06     -1.943501e+06   
395912      -4.766243e+06      5.708557e+06     -3.550115e+06   
2539047      1.173970e+06     -2.348325e+06      2.023347e+06   

         pca_embedding_15  pca_embedding_16  pca_embe

## Create user-article matrix

## Compute Interaction Matrix:
##### Compute the recommendation score for each item i for the user u using the learned embeddings.
##### The recommendation score can be calculated as the dot product (similarity) between the user embedding u_emb and the item embedding v_i for each item i.
#### Score(𝑢,𝑖)=𝑢_𝑒𝑚𝑏^𝑇 × 𝑣𝑖

#### Where:
#### - u_emb: User embedding vector for user u.
#### - v_i: Item embedding vector for item i.
#### -  ^T: Transpose operation.
#### -  \times: Dot product.

In [42]:
# Compute user-article interaction matrix X using matrix multiplication
X = np.dot(df_users_embeddings, df_articles_embeddings.T)

# X is now a matrix of shape (N_users, N_articles) containing combined embeddings

In [43]:
X_df = pd.DataFrame(X, index = df_users_embeddings.index.values, columns = df_articles_embeddings.index.values)

In [44]:
X_df.head()

3037230       3044020       3057622       3073151       3193383  \
13538  -1.658952e+06  1.033794e+07  4.996713e+06  5.914584e+06 -3.048869e+06   
58608  -4.200500e+05 -7.116461e+05  2.071218e+05 -1.137468e+06  3.493051e+06   
95507  -1.881312e+06 -1.811155e+05  1.282839e+06 -2.874994e+06 -6.161579e+06   
106588 -4.913770e+05  3.072927e+05  2.103026e+05 -9.935449e+05  4.094621e+06   
617963  2.435188e+06  1.119679e+06  4.118558e+06  4.722468e+06  7.045818e+06   

             3196611       3200325       3200913       3209311       3209357  \
13538  -7.431156e+06  4.479062e+05 -2.224360e+06 -2.535303e+06 -2.404891e+06   
58608   3.013280e+06  1.679346e+06  2.751666e+05  2.909303e+06  2.038927e+06   
95507  -8.582682e+06 -6.281714e+06 -6.439982e+06 -6.984851e+06 -5.437276e+06   
106588  3.599134e+06  1.721970e+06  4.297899e+05  3.306646e+06  2.168372e+06   
617963  2.955140e+06  4.947647e+06  3.662183e+06  5.995478e+06  3.415259e+06   

             3223114       3251664       3971783       3977720       3983641  \
13538   4.887447e+04 -4.574709e+05  5.366169e+06  4.872022e+06 -2.072906e+06   
58608   5.350524e+05  3.079472e+05 -1.395485e+06  1.092166e+06  1.296430e+05   
95507  -2.886094e+06  2.799794e+06  1.562948e+06 -2.337705e+04 -6.348997e+06   
106588  3.352167e+05  4.538038e+04 -1.593426e+06  4.704334e+05  2.655835e+05   
617963  3.721898e+06  4.061586e+06  2.471122e+06  6.696044e+06  8.491937e+05   

             3987418       3988589       3993395       3994264       3997229  \
13538  -4.034658e+05 -3.731755e+06  5.492658e+06 -2.120067e+06 -5.452614e+05   
58608   1.076771e+06  9.488794e+05  1.144477e+06  8.728114e+03  3.648189e+06   
95507  -5.044908e+06 -1.020974e+07 -1.223642e+06 -5.898759e+06 -5.304099e+06   
106588  1.214576e+06  1.151527e+06  1.386051e+06 -9.563065e+04  3.559023e+06   
617963  2.650528e+05 -1.641130e+06  5.474896e+06  3.850363e+06  1.076413e+06   

             3997233       3998680       4000567       4000823       4003163  \
13538  -4.792998e+06 -3.472136e+06  3.360423e+06 -2.068461e+06 -1.127215e+06   
58608   3.358067e+06 -6.347764e+05  1.274523e+06 -6.814534e+05  3.161672e+06   
95507  -6.600453e+06 -1.017100e+06 -1.615692e+06 -1.215612e+06 -5.599398e+06   
106588  3.440536e+06 -8.561693e+05  9.429392e+05 -1.221847e+06  3.207318e+06   
617963  4.654931e+06 -3.681088e+05  3.813230e+06  1.866283e+06  4.078073e+06   

             4003362       4003431       4003926       4007811       4008213  \
13538  -1.800178e+06  1.807161e+06  4.049839e+06  6.515428e+06 -1.382656e+06   
58608   2.418589e+06  6.601552e+05 -8.916395e+05  3.738521e+05  1.536229e+06   
95507  -6.121361e+06 -1.115598e+06  6.365551e+06 -4.281280e+06 -4.157553e+06   
106588  2.275364e+06  6.962877e+05 -1.255224e+06  2.033730e+05  9.687492e+05   
617963  2.846502e+06  3.823766e+06  1.419126e+06  3.023145e+06  1.821966e+06   

             4009177       4014381       4021392       4024289       4024449  \
13538  -1.915653e+06 -3.175284e+06  6.556350e+06  5.482843e+06  8.204057e+06   
58608   2.737179e+06 -3.423217e+04 -2.410033e+06 -1.270405e+05 -1.616439e+05   
95507  -5.934536e+06 -4.496176e+06  9.278821e+05  1.312670e+06 -2.335483e+06   
106588  2.508278e+06 -3.960305e+05 -2.134689e+06  3.442029e+05 -1.641702e+05   
617963  4.485181e+06  1.724349e+06  2.942861e+06  2.246378e+06  3.346403e+06   

             4026960       4035059       4035605       4040731       4040737  \
13538   2.611164e+06 -1.132323e+05  2.881963e+06  2.265858e+06  1.958498e+06   
58608   1.184789e+06 -3.117275e+06  3.421217e+05  1.647514e+06  3.334983e+05   
95507  -6.705957e+06 -6.978409e+05  4.055494e+06 -3.609979e+06 -4.898884e+06   
106588  1.332639e+06 -3.573802e+06  5.833087e+05  2.168488e+06  7.068476e+05   
617963  4.691961e+06  2.426483e+06  4.505632e+06  6.712664e+06  6.680139e+06   

             4043121       4044042       4045439       4048845       4050800  \
13538   3.832579e+06  2.170886e+06 -2.148325e+06  7.588059e+06  3.971869e+05   
58608

#### Singular Value Decomposition (SVD): SVD is used to decompose the user-movie interaction matrix X into three matrices: U (user embeddings), sigma (singular values), and Vt (transposed movie embeddings).
#### Number of Latent Factors (k): Specify the number of latent factors (embedding dimensions) to use in the matrix factorization.
#### Reconstruction of Embeddings:
##### - Compute sigma_diag, a diagonal matrix containing the singular values.
##### - Compute U_train (user embeddings) by multiplying U with the square root of sigma_diag.
##### - Compute V_train (article embeddings) by multiplying the square root of sigma_diag with Vt.

In [45]:
from scipy.sparse.linalg import svds

# Perform Singular Value Decomposition (SVD) on the user-movie interaction matrix X
# X should be a dense matrix
k = 300  # Number of latent factors (embedding dimensions)

U, sigma, Vt = svds(X_df.values, k=k)  # Perform SVD, obtaining U, sigma, Vt

# Diagonalize the singular values sigma to create a diagonal matrix
sigma_diag = np.diag(sigma)

# Reconstruct the user and movie embeddings
U_train = np.dot(U, np.sqrt(sigma_diag))  # User embeddings
V_train = np.dot(np.sqrt(sigma_diag), Vt)  # Article embeddings

In [46]:
U_train_df =  pd.DataFrame(U_train, index = X_df.index.values)
V_train_df =  pd.DataFrame(V_train.T, index = X_df.columns.values)

## Save of the embeddings

In [48]:
u_train_file_path = './files/csv/u_train_embeddings.csv'
v_train_file_path = './files/csv/v_train_embeddings.csv'

U_train_df.to_csv(u_train_file_path)
V_train_df.to_csv(v_train_file_path)